https://github.com/MichaelAllen1966/learninghospital/blob/master/simpy_envs/env_simple_hospital_bed_1.py

I recently came across this simulation implementation of this study where they used SimPy and were able to work it within a `step` framework. 

I read through the study and I found that the key idea that enabled it was that the `env.run()` was inside the `step()` function. And the key idea is *drumrolls* that the environment is run only for one time step at a time (or a constant number of time steps) 

I'm going to try and implement this using the environment that I have on SimPy already. 

# Notes

Current problems/questions
- When an action is rejected, we have to pause the production. Currently it is not pausing. It is going ahead with the next first product in the queue. [More info](https://simpy.readthedocs.io/en/latest/topical_guides/process_interaction.html#sleep-until-woken-up)
    

-----

Solved problems
- `prod_and_requests` is empty when checking for check_env function. Look into it
    - This is because i'm appending to prod_and_requests inside the envGym but while checking the env, envGym is not defined. This is the problem. Why do I have envGym inside the class?
- What is the flow of the current customEnv?
- How to ensure that the action suggested by DQN is taken by the algorithm?
    - Print action taken (Step function)
    - Print action chosen by the RL agent
    - SOLVED: Now I use the same variable `self.current_action` to record the input action and then execute it when necessary. 

# OpenAI Gym environment 

Gym format 

## Choosing a product environment 

In [ ]:
import gym
from gym import spaces
import numpy as np 
import simpy 
import random



In [ ]:
import gym
from gym import spaces
import numpy as np 
import simpy 
import random

 
        
class CustomEnv(gym.Env):
    metadata = {'render.modes': ['human']}
    def __init__(self):
        super(CustomEnv, self).__init__()
        #random.seed(42)
        # Define action and observation space
        # They must be gym.spaces objects
        # Example when using discrete actions:

        # initially the observation space is zero. I will append as the products are initialized.
        #print("Observation space sample ",self.observation_space.sample())
        #self.observation_space = spaces.Box(low=0, high=255,shape=(2, 2), dtype=np.uint8)
##------------------------------------------------------------------------------------------------
##----------------------------------------SIMPY STUFF---------------------------------------------
##------------------------------------------------------------------------------------------------

        
#        self.action = env.process(self.production())
        self.NUM_PRODUCTS = 20
        self.next_time_stop = 0
        self.prod_and_requests = []
        # Defining the observation and action spaces 
        # action space for choosing product 
         self.action_space = spaces.Discrete(self.NUM_PRODUCTS)
        # action space for Yes/No action space 
        # self.action_space = spaces.Discrete(2)
        self.observation_space = spaces.Box(0,1,shape = (self.NUM_PRODUCTS,1),
                                            dtype = np.float32)
    
    def getObservation(self):
        # Calculate the states 
        states = []
        if self.machine.queue != None:
            for i in (self.machine.queue):
                states.append((self.relater(i)).number)
        #Checking the length of the states and filling the rest with zeros
        if len(states) < self.NUM_PRODUCTS:
            for i in range(self.NUM_PRODUCTS - len(states)):
                states.append(0)
        states = np.array(states).reshape(self.NUM_PRODUCTS,1)
        return states
    
    def doneFn(self):
        # So the condition is, 
        #(no items in queue1 + queue2 + ...) AND 
        #(no machine is running)
        if self.machine.queue != None:
            lenQueue = len(self.machine.queue )
        else:
            lenQueue = 0 
        lenMachinesUsed = self.machine.count
        if lenQueue == 0 and lenMachinesUsed == 0:
            #print("length of queue ",lenQueue,"Machines used ", lenMachinesUsed)
            return True
        else:
            #print("length of queue ",lenQueue,"Machines used ", lenMachinesUsed)
            return False
    
    def step(self):
        self.action_taken = False 
        self.info = {}
        self.next_time_stop += self.time_step
        self.envSimpy.run(until =self.next_time_stop)

        # Calculate states
        observation = self.getObservation()
        reward = 1 
        done = self.doneFn()
        info = self.info
        if self.action_taken == True:
            #print("Taking this action ", self.action)
            pass
        else:
            pass
            #print('No action was taken')
        return observation, reward, done, info
    # ----------------------------------------------------------------
    def reset(self):
        self.envSimpy = simpy.Environment()
        self.machine = simpy.Resource(self.envSimpy,capacity = 1)
        self.time_start = self.envSimpy.now
        print("This is the time ",self.time_start)
        self.next_time_stop = self.time_start + 2
        self.time_step = 1 
        self.time_step_terminal = self.time_start + 100
        self.current_action = 0
        print('the time now is ', self.time_start)
        
        self.instances = []
        for i in range(self.NUM_PRODUCTS):
            self.instances.append(self.product(self,self.envSimpy,'Product_%d' % i,i/100, self.machine))
        # i is divided by hundred because the number has to obey the observation_space criteria which is 1 to 1. 
        self.observation = self.getObservation()
        
        return np.array(self.observation)  # reward, done, info can't be included

    
    def render(self, mode='human'):
        myFrame = ""
        #myFrame = "_:_:_:_:_:_:_:_:01:19:18:_:01:02:03::|02|"
        
        for item in enumerate(self.machine.queue):
            product = self.relater(item[1])
            myFrame = myFrame + str(int((product.number)*100)) +':'
        for i in range(self.NUM_PRODUCTS-len(self.machine.queue)):
            myFrame = myFrame + 'x' +':'
        if self.relater(self.machine.users[0]) == None:
            prod_in_machine = 0
            machine_text = prod_in_machine 
        else:
            prod_in_machine = self.relater(self.machine.users[0])
            machine_text = int(prod_in_machine.number*100)
        myFrame = myFrame + ":|" + str(machine_text) + "|"
        return myFrame
    
    def close (self):
        return True
    
    # write the following functions
    
    
    def isLegal(self,action):
        return
    def isExecutable(self, action):
        return True 
    def interpretQueue(self):
        return True 
    def choose_action(self):
            # sampling until we get a legal action
        while True:
            self.action = envGym.action_space.sample()
            if (envGym.machine.queue != None):
                if len(envGym.machine.queue) != 0:
                    if len(envGym.machine.queue)-1 < self.action:
                        # the action is illegal -> sample again
                        #print("machine queue is ", envGym.machine.queue)
                        #print("length of machine queue ",len(envGym.machine.queue)-1,"action " , self.action )
                        pass
                    else:
                        break
                else:
                    self.action = None
                    break
        return self.action
    
    def take_action(self):
        # arrange the self.machine.queue based on the self.current_action
        # to do 
        # Do something about illegal action
        if self.current_action != None:
            if self.machine.queue != None:
                # rearrange queue
                #print("Initial queue with length  ", len(self.machine.queue))
                #print("test4 queue ", len(self.machine.queue), "action " , self.current_action)
                product_high_priority = (self.machine.queue)[(self.current_action)]
                #print("high priority product ", product_high_priority, "Position was ", self.current_action)
                (self.machine.queue).pop(self.current_action)
                self.machine.queue.insert(0,product_high_priority)
                #print("Edited queue ")

                # change the action_taken bit 
                #print('Does the queue length remain the same ?', len(self.machine.queue))
                envGym.action_taken = True
                return self.machine.queue
            else: 
                self.info = {"Queue is empty, no action taken"}
                #print("Queue is empty, no action taken")
                return self.machine.queue
        else:
            return self.machine.queue
       

    # A function to relate products and requests
    def relater(self,item):
        output_item = None

        if type(item) == simpy.resources.resource.Request:
            for i, j in enumerate(self.prod_and_requests):
                if j[1] == item:
                    output_item = j[0]
                    return output_item
        else:
            #print('Input Process object is ')
            for i, j in enumerate(self.prod_and_requests):
                if j[0] == item:
                    output_item = j[1]
                    return output_item

    class product(object):
        def __init__(self, envGym, envSimpy, name, number, machine):
            # Creating the required resources and environment
            self.envSimpy = envSimpy
            self.prod_type = random.randint(1,3) # the product type of the product.
            self.prod_state = 1 # the state of production. 1 implies raw material. 2 implies first operation done and so on. 
            self.production_time = random.randint(1,8)  
            self.name = name
            self.number = number
            self.machine = machine 
            self.production_end = random.randint(1,90)
            self.action = self.envSimpy.process(self.production())

            # move this into the main class
        def production(self):
            # the first step in production is requesting for a machine
            #print('entered production ' + self.name)
            with self.machine.request() as req:
                envGym.prod_and_requests.append([self,req])
                #print('waiting for the request to succeed ' + str(self.name))
                yield req
                print('Start production of ' + str(self.name) + ' at '+ str(self.envSimpy.now)  )
                print('Production time is ' + str(self.production_time))
                yield self.envSimpy.timeout(self.production_time)
                self.tardiness = self.production_end - self.envSimpy.now
                # End of production
                print('End production of ' + str(self.name) + ' at ' + str(self.envSimpy.now))
                print('\n')
                # Taking the chosen action
                envGym.current_action = envGym.choose_action()
                envGym.machine.queue = envGym.take_action()
            #print('Remaining products to produce ')
            #print((self.machine.queue)) 



## Yes/No Environment

In [1]:
import gym
from gym import spaces
import numpy as np 
import simpy 
import random

In [54]:
class CustomEnv(gym.Env):
    metadata = {'render.modes': ['human']}
    def __init__(self):
        super(CustomEnv, self).__init__()
        #random.seed(42)
        # Define action and observation space
        # They must be gym.spaces objects
        # Example when using discrete actions:

        # initially the observation space is zero. I will append as the products are initialized.
        #print("Observation space sample ",self.observation_space.sample())
        #self.observation_space = spaces.Box(low=0, high=255,shape=(2, 2), dtype=np.uint8)
##------------------------------------------------------------------------------------------------
##----------------------------------------SIMPY STUFF---------------------------------------------
##------------------------------------------------------------------------------------------------

        
#        self.action = env.process(self.production())
        self.NUM_PRODUCTS = 20
        self.next_time_stop = 0
        self.prod_and_requests = []
        self.reward = 0
        self.cumulative_reward = 0
        # Defining the observation and action spaces 
        # action space for choosing product 
        # self.action_space = spaces.Discrete(self.NUM_PRODUCTS)
        # action space for Yes/No action space 
        self.action_space = spaces.Discrete(2)
        self.observation_space = spaces.Box(0,1,shape = (self.NUM_PRODUCTS,),
                                            dtype = np.float32)
    
    def getObservation(self):
        # Calculate the states 
        states = []
        if self.machine.queue != None:
            for i in (self.machine.queue):
                states.append((self.relater(i)).number)
        #Checking the length of the states and filling the rest with zeros
        if len(states) < self.NUM_PRODUCTS:
            for i in range(self.NUM_PRODUCTS - len(states)):
                states.append(0)
        states = np.array(states).reshape(self.NUM_PRODUCTS,1)
        
        states = states.flatten()
        return states
    

# --------------------------------------------------------------------------------------------------------------------------------
# -----------------------OpenAI Gym functions--------------------------------------------------------------------
# --------------------------------------------------------------------------------------------------------------------------------
    
    def step(self, action):
        print("New action from the agent")
        #print("-------------------------------------------------------------------------------")
        #print("Action chosen by the RL agent ", action)
        
        # Define params
        self.current_action = action
        self.action_taken = False 
        self.info = {}
        #print("Current user of the machine ", envGym.machine.users)
        #print(envGym.machine.queue)
        self.next_time_stop += self.time_step
        self.envSimpy.run(until = self.next_time_stop)
        # Get the observation states
        observation = self.getObservation()
        done = self.doneFn()
        info = self.info
        self.cumulative_reward += self.reward
        
        return observation, self.reward, done, info
    
    # ----------------------------------------------------------------
    def reset(self):
        self.envSimpy = simpy.Environment()
        self.machine = simpy.Resource(self.envSimpy,capacity = 1)
        self.time_start = self.envSimpy.now
        self.next_time_stop = self.time_start + 1
        self.time_step = 1 
        self.time_step_terminal = self.time_start + 100
        self.current_action = 0
        self.instances = []
        
        for i in range(self.NUM_PRODUCTS):
            self.instances.append(self.product(self,self.envSimpy,'Product_%d' % i,i/100, self.machine))
        
        # i is divided by hundred because the number has to obey the observation_space criteria which is 1 to 1. 
        self.observation = self.getObservation()
        
        return np.array(self.observation)  # reward, done, info can't be included

    
    def render(self, mode='human'):
        myFrame = ""
        #myFrame = "_:_:_:_:_:_:_:_:01:19:18:_:01:02:03::|02|"
        
        for item in enumerate(self.machine.queue):
            product = self.relater(item[1])
            myFrame = str(int((product.number)*100)) +':'+ myFrame
        for i in range(self.NUM_PRODUCTS-len(self.machine.queue)):
            myFrame =  'x' +':' + myFrame
        if self.relater(self.machine.users[0]) == None:
            prod_in_machine = 0
            machine_text = prod_in_machine 
        else:
            prod_in_machine = self.relater(self.machine.users[0])
            machine_text = int(prod_in_machine.number*100)
        myFrame = myFrame +  "  |" + str(machine_text) + "|"
        return myFrame

# --------------------------------------------------------------------------------------------------------------------------------
# -----------------------Miscellaneous functions--------------------------------------------------------------------
# --------------------------------------------------------------------------------------------------------------------------------
    def doneFn(self):
        # So the condition is, 
        #(no items in queue1 + queue2 + ...) AND 
        #(no machine is running)
        
        if self.machine.queue != None:
            lenQueue = len(self.machine.queue)
        else:
            lenQueue = 0 
        lenMachinesUsed = self.machine.count
        if lenQueue == 0 and lenMachinesUsed == 0:
            #print("length of queue ",lenQueue,"Machines used ", lenMachinesUsed)
            return True
        else:
            #print("length of queue ",lenQueue,"Machines used ", lenMachinesUsed)
            return False
        
    # A function to relate products and requests
    def relater(self,item):
        output_item = None
        # If the input is a request
        if type(item) == simpy.resources.resource.Request:
            for i, j in enumerate(self.prod_and_requests):
                if j[1] == item:
                    output_item = j[0]
                    return output_item
        else: #if the input is a product 
            for i, j in enumerate(self.prod_and_requests):
                if j[0] == item:
                    output_item = j[1]
                    return output_item    

# --------------------------------------------------------------------------------------------------------------------------------
# -----------------------Action related functions--------------------------------------------------------------------
# --------------------------------------------------------------------------------------------------------------------------------
    def choose_action(self):
        # sampling until we get a legal action
        self.action = envGym.action_space.sample()
        return self.action
    
    def take_action(self):
        # arrange the self.machine.queue based on the self.current_action
        self.action_taken = True 
        #print("Taking the action....")
        #print("Input machine queue ", self.machine.queue)
        if len(self.machine.queue) != 0:
            if self.current_action == 0: # if the answer is yes
                #print("Action accepted")
                #print("The first item in the queue ", self.relater(self.machine.queue[0]).name, " is accepted ")
                #print("Output machine queue ", self.machine.queue)
                return self.machine.queue # return the machine queue as is
            elif self.current_action == 1: # if the answer is no 
                # rearrange the machine queue 
                # Take the first element in the machine queue and put it in the last pos. 
                self.machine.queue.insert(len(self.machine.queue), self.machine.queue.pop(0))
                #print("Action rejected")
                #print("Output machine queue ", self.machine.queue)
                #print("The first item in the queue ", self.relater(self.machine.queue[0]).name, " is rejected ")
                return self.machine.queue
        else:
            return self.machine.queue

# --------------------------------------------------------------------------------------------------------------------------------
# -----------------------Product class definition--------------------------------------------------------------------
# --------------------------------------------------------------------------------------------------------------------------------

    class product(object):
        def __init__(self, envGym, envSimpy, name, number, machine):
            
            # Creating the required resources and environment
            self.envSimpy = envSimpy
            self.prod_type = random.randint(1,3) # the product type of the product.
            self.prod_state = 1 # the state of production. 1 implies raw material. 2 implies first operation done and so on. 
            self.production_time = random.randint(1,8)  
            self.name = name
            self.number = number
            self.machine = machine 
            self.production_end = random.randint(1,90)
            self.action = self.envSimpy.process(self.production())
            
            #self.action_taken_event = envSimpy.event
            # Defining Events        
            #self.action_accepted_event = envSimpy.event()            
            # Defining processes
            #self.check_accepted_proc = envSimpy.process(self.check_accepted(envSimpy))


            
        def production(self):
            # the first step in production is requesting for a machine
            #print('entered production ' + self.name)
            with self.machine.request() as req:
                envGym.prod_and_requests.append([self,req])
                #print('waiting for the request to succeed ' + str(self.name))
                yield req
                print('Start production of ' + str(self.name) + ' at '+ str(self.envSimpy.now)  )
                #print("Request of the product ", envGym.relater(self))
                print('Production time is ' + str(self.production_time))
                yield self.envSimpy.timeout(self.production_time)
                self.tardiness = self.envSimpy.now - self.production_end   # -ve is good; +ve is bad 
                
                # End of production 
                print('End production of ' + str(self.name) + ' at ' + str(self.envSimpy.now))
                
                # Pass time when the action chosen by the agent is rejection
                i = 0
                while True:
                    i += 1
                    if envGym.current_action == 1: #rejected
                        yield self.envSimpy.timeout(1)
                        print("Action rejected; Passing time by 0.1 ", i)
                    else: 
                        print("Action accepted")
                        break
                
                # Decide the reward 
                if self.tardiness > 0:
                    envGym.reward = 10 
                else: 
                    envGym.reward = 0
                
                # Production has ended now I have to take the next action using take_action()
                envGym.machine.queue = envGym.take_action()
                #envGym.machine.queue = []
                
                
        
        def check_accepted(self, envSimpy): # sleep and production
            while True: # check in a continuous loop 
                if envGym.current_action == 0: # Is action accepted?
                    print("Action is accepted")
                    # Unsleeping the process 
                    self.action_accepted_event.succeed()
                    self.action_accepted_event = envSimpy.event()            
                else:
                    print("Action is rejected")
                    pass
        
        def passivate_production(self):
            while True:
                print("Passivating production at ", self.envSimpy.now)
                yield self.reactivate_production
                print("Production reactivate at ", self.envSimpy.now)
            #print('Remaining products to produce ')
            #print((self.machine.queue)) 

## Testing the environment 

In [55]:
import gym
from gym import error, spaces, utils
from gym.utils import seeding
#random.seed(42)
envGym = CustomEnv()
obs = envGym.reset()
frames = [] # for animation

# Add another while loop above the current one for EPOCHS
while True: # This while is for one full cycle of products (20 nos, currently)

    # Choosing the action
    action = envGym.action_space.sample()
    
    # Taking a step

    obs, reward, done, info = envGym.step(action) # the env here is gym
    # Note that in the above step function, i'm passing 1. 
    # It has no relevance to the action that will be taken. It is just to satisfy the OpenAI Gym requirements
    #print("Action chosen by the agent ", action)
    #print("Action taken by the environment ", )
    if done:
        print("Goal reached! ", "reward= ", reward)
        print("The env time is ", envGym.envSimpy.now)
        sum_Tardiness = 0 
        for i in range(20):
            #print(envGym.instances[i].tardiness)
            sum_Tardiness = sum_Tardiness + envGym.instances[i].tardiness
            print('Tardiness value of ', i, 'is ',envGym.instances[i].tardiness )
            
        print('Mean tardiness for this episode is ', sum_Tardiness)
        print('Total reward for this episode is ', envGym.cumulative_reward)
        break
    else:
        frames.append({
            'frame': envGym.render(mode='ansi'),
            'state': obs,
            'action': envGym.current_action,
            'reward': reward
            }
        )        

New action from the agent
Start production of Product_0 at 0
Production time is 1
End production of Product_0 at 1
New action from the agent
Action rejected; Passing time by 0.1  1
New action from the agent
Action rejected; Passing time by 0.1  2
New action from the agent
Action rejected; Passing time by 0.1  3
New action from the agent
Action rejected; Passing time by 0.1  4
New action from the agent
Action rejected; Passing time by 0.1  5
New action from the agent
Action rejected; Passing time by 0.1  6
Action accepted
Start production of Product_1 at 7
Production time is 2
New action from the agent
New action from the agent
End production of Product_1 at 9
Action accepted
Start production of Product_2 at 9
Production time is 3
New action from the agent
New action from the agent
New action from the agent
End production of Product_2 at 12
Action accepted
Start production of Product_3 at 12
Production time is 7
New action from the agent
New action from the agent
New action from the age

### Rendering

In [50]:
from IPython.display import clear_output
from time import sleep

def print_frames(frames):
    for i, frame in enumerate(frames):
        clear_output(wait=True)
        print(frame['frame'])
        #print(f"Timestep: {i + 1}")
        #print(f"State: {frame['state']}")
        #print(f"Action: {frame['action']}")
        #print(f"Reward: {frame['reward']}")
        sleep(0.7)
        
print_frames(frames)

x:x:x:2:19:18:17:16:15:14:13:12:11:10:9:8:7:6:5:4:  |3|


KeyboardInterrupt: 

Calculating the tardiness

The following is the code to test if the environment conforms to the OpenAI format. 

In [ ]:
from stable_baselines.common.env_checker import check_env
random.seed(42)
envGym = CustomEnv()
# It will check your custom environment and output additional warnings if needed
check_env(envGym, warn= True)

# RL Algorithms

## DQN

In [51]:
envGym.reset()

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0])

In [52]:
import gym
from stable_baselines import DQN
from stable_baselines.common.evaluation import evaluate_policy



### Training the RL model

In [53]:
%%time
# Instantiate the agent
model = DQN('MlpPolicy', envGym, learning_rate=1e-3, prioritized_replay=True, verbose=1)
# Train the agent
model.learn(total_timesteps= 10000) #int(2e5))
# Save the agent
model.save("dqn_jobshop")
del model  # delete trained model to demonstrate loading

-------------------------------------------------------------------------------
Action chosen by the RL agent  1
Start production of Product_0 at 0
Production time is 7


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1
End production of Product_0 at 7
Taking the action....
Input machine queue  [<Request() object at 0x13a7b1f60>, <Request() object at 0x139be17b8>, <Request() object at 0x13b9364a8>, <Request() object at 0x13b9367b8>, <Request() object at 0x13b9369b0>, <Req

-------------------------------------------------------------------------------
Action chosen by the RL agent  0
End production of Product_13 at 100
Taking the action....
Input machine queue  []


-------------------------------------------------------------------------------
Action chosen by the RL agent  0
Start production of Product_0 at 0
Production time is 2
End production of Product_0 at 2
Taking the action....
Input machine queue  [<Request() object at 0x13b23f0f0>, <Request() object at 0x13a7cc358>, <Request() object at 0x13b613ac8>, <Request() object at 0x10fcd0080>, <Request() object at 0x13b181240>, <Request() object at 0x13b181c88>, <Request() object at 0x13b181e48>, <Request() object at 0x13b181c18>, <Request() object at 0x13b1816a0>, <Request() object at 0x13b181588>, <Request() object at 0x13b181c50>, <Request() object at 0x13b181fd0>, <Request() object at 0x13b181390>, <Request() object at 0x13b1815c0>, <Request() object at 0x13b181438>, <Request() object at 0x13b181208

-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  0
End production of Product_15 at 75
Taking the action....
Input machine queue  [<Request() object at 0x13b181208>, <Request() object at 0x13b181e10>, <Request() object at 0x13b1810b8>, <Request() object at 0x13a711400>, <Request() object at 0x13b181c18>, <Request() object at 0x13b181c50>]
Action accepted
Output 

-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  1
End production of Product_7 at 31
Taking the action....
Input machine queue  [<Request() object at 0x13b1b8c88>, <Request() object at 0x13b1b84e0>, <Request() object at 0x13b1b8dd8>, <Request() object at 0x13b1b8cc0>, <Request() object at 0x13b1b8f98>, <Request() object at 0x13a6c1da0>, <Request() object at 0x1

-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1
End production of Product_6 at 111
Taking the action....
Input machine queue  [<Re

...


-------------------------------------------------------------------------------
Action chosen by the RL agent  1
End production of Product_4 at 17
Taking the action....
Input machine queue  [<Request() object at 0x13b34f588>, <Request() object at 0x13b34f320>, <Request() object at 0x13b34f2b0>, <Request() object at 0x13b34f0f0>, <Request() object at 0x13b34f470>, <Request() object at 0x13b34fa58>, <Request() object at 0x13b34fcc0>, <Request() object at 0x13b34fe10>, <Request() object at 0x13b36df60>, <Request() object at 0x13b36def0>, <Request() object at 0x13b36de80>, <Request() object at 0x13b36d9b0>, <Request() object at 0x13b36dfd0>, <Request() object at 0x13b36d588>, <Request() object at 0x13b36dc50>]
Action rejected
Output machine queue  [<Request() object at 0x13b34f320>, <Request() object at 0x13b34f2b0>, <Request() object at 0x13b34f0f0>, <Request() object at 0x13b34f470>, <Request() object at 0x13b34fa58>, <Request() object at 0x13b34fcc0>, <Request() object at 0x13b34fe10>,

-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1
End production of Product_16 at 52
Taking the action....
Input machine queue  [<Request() object at 0x13b36dfd0>, <Request() object at 0x13b36d588>, <Request() object at 0x13b36dc50>, <Request() object at 0x13b34f588>, <Request() object at 0x13b34f2b0>, <Request() object at 0x13b34f470>, <Request() object at 0x

-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1
End production of Product_12 at 90
Taking the action....
Input machine queue  [<Request() object at 0x13b34f2b0>]
Action rejected
Output machine queue  [<Request() object at 0x13b34f2b0>]
Start production of Product_7 at 90
Production time is 2


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0
End production of Product_7 at 92
Taking the action....
Input machi



-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1
End production of Product_4 at 20
Taking the action....
Input machine queue  [<Request() object at 0x13b36db70>, <Request() object at 0x13b36d208>, <Request() object at 0x13b36d828>, <Request() object at 0x13b36d390>, <Request() object at 0x13b36da90>, <Request() object at 0x13b36da58>, <Request() object at 0x13b36deb8>, <Request() object at 0x13b36d710>, <Request() object at 0x13b36d278>, <Request() object at 0x13b36dc18>, <Request() object at 0x13b36d6d8>, <Request() object at 0x13b36d320>, <Request() object at 0x13b36d630>, <Request() object at 0x139beb7f0>, <Request() object at 0x139beb940>]
Action rejected
Output machine queue  [<Request() ob

-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0
End production of Product_14 at 51
Taking the action....
Input machine queue  [<Request() object at 0x13b36d6d8>, <Request() object at 0x13b36d320>, <Request() object at 0x13b36d630>, <Request() ob

### Loading the training RL model

In [54]:
# Load the trained agent
model = DQN.load("dqn_jobshop")

# Evaluate the agent
mean_reward, std_reward = evaluate_policy(model, envGym, n_eval_episodes=10)
print(mean_reward, std_reward)
# Enjoy trained agent
obs = envGym.reset()
for i in range(1000):
    action, _states = model.predict(obs)
    obs, rewards, dones, info = envGym.step(action)
#envGym.render()

Loading a model without an environment, this model cannot be trained until it has a valid environment.
-------------------------------------------------------------------------------
Action chosen by the RL agent  0
Start production of Product_0 at 0
Production time is 1
End production of Product_0 at 1
Taking the action....
Input machine queue  [<Request() object at 0x13cdd7ac8>, <Request() object at 0x13a774630>, <Request() object at 0x13cdcdef0>, <Request() object at 0x13cdcdcf8>, <Request() object at 0x13cdcda58>, <Request() object at 0x13cdd7358>, <Request() object at 0x13cdd7400>, <Request() object at 0x13cdd74a8>, <Request() object at 0x13cdd7550>, <Request() object at 0x13cdd75f8>, <Request() object at 0x13cdd76a0>, <Request() object at 0x13cdd7748>, <Request() object at 0x13cdd77f0>, <Request() object at 0x13cdd7898>, <Request() object at 0x13cdd7d68>, <Request() object at 0x13cdd7e10>, <Request() object at 0x13cdd7eb8>, <Request() object at 0x13cdd7f60>, <Request() object at 


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0
End production of Product_10 at 36
Taking the action....
Input machine queue  [<Request() object at 0x13cdd76a0>, <Request() object at 0x13cdd7748>, <Request() object at 0x13cdd77f0>, <Request() object at 0x13cdd7898>, <Request() object at 0x13cdd7d68>, <Request() object at 0x13cdd7e10>, <Request() object at 0x13cdd7eb8>, <Request() object at 0x13cdd7f60>, <Request() object at 0x13cdd7cf8>, <Request() object at 0x13cdcda58>, <Request() object at 0x13cdd7400>, <Request() object at 0x13cdd7550>]
Action accepted
Output machine queue  [<Re


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0
End production of Product_17 at 83
Taking the action....
Input machine queue  [<Request() object at 0x13cdd7cf8>, <Request() object at 0x13cdd7400>, <Request() object at 0x13cdd77f0>]
Action accepted
Output machine queue  [<Request() object at 0x13cdd7cf8>, <Request() object at 0x13cdd7400>, <Request() object 


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0
End production of Product_11 at 29
Taking the action....
Input machine queue  [<Request() object at 0x13cdda710>, <Request() object at 0x13cdda828>, <Request() object at 0x13cdda8d0>, <Request() object at 0x13cdda978>, <Request() object at 0x13cddaa20>, <Request() object at 0x13cddaac8>, <Request() object at 0x13cddab70>, <Request() object at 0x13cddac18>, <Request() object at 0x13cdda240>, <Request() object at 0x13cdda4e0

-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1
End production of Product_19 at 72
Taking the action....
Input machine queue  [<Request() object at 0x13cdda4e0>, <Request() object at 0x13cdda828>]
Action rejected
Output machine queue  [<Request() object at 0x13cdda828>, <Request() object at 0x13cdda4e0>]
Start production of Product_13 at 72
Production time is 3


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1


-------------------------------------------------------------------------------
Action chosen by the RL agent  1
End production of Product_13 at 75
Taking the action....
Input machine queue  [<Request() object at 0x13cdda4e0

...

-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------



-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------

-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------
Action chosen by the RL agent  0


-------------------------------------------------------------------------------


In [55]:
mean_reward, std_reward

(108.0, 24.413111231467404)

### Other code

In [ ]:
# setting the machine_busy bit
        if envGym.machine.users != []:
            self.machine_busy = True
        else:
            self.machine_busy = False
        
        
        if self.machine_busy == True:
            self.reward = 0            
            # Run the simulation by 1 time unit
            self.next_time_stop += self.time_step
            self.envSimpy.run(until = self.next_time_stop)
            
            # Calculate states
            observation = self.getObservation() 
            done = self.doneFn()
            info = self.info
            self.cumulative_reward += self.reward
            print('\n')
            
        elif self.machine_busy == False:
            if self.current_action == 1: # if rejected don't enter the simulation
                # Rearrange the machine queue
                envGym.machine.queue = envGym.take_action()
                
                # Get the observation states
                observation = self.getObservation()
                done = self.doneFn()
                info = self.info
                
            else: # if accepted rearrange the queue and run simulation
                envGym.machine.queue = envGym.take_action()
                
                
                # Run the simulation by 1 time unit

### The entire environment code from Thursday, 10 December 2020 

In [ ]:
class CustomEnv(gym.Env):
    metadata = {'render.modes': ['human']}
    def __init__(self):
        super(CustomEnv, self).__init__()
        #random.seed(42)
        # Define action and observation space
        # They must be gym.spaces objects
        # Example when using discrete actions:

        # initially the observation space is zero. I will append as the products are initialized.
        #print("Observation space sample ",self.observation_space.sample())
        #self.observation_space = spaces.Box(low=0, high=255,shape=(2, 2), dtype=np.uint8)
##------------------------------------------------------------------------------------------------
##----------------------------------------SIMPY STUFF---------------------------------------------
##------------------------------------------------------------------------------------------------

        
#        self.action = env.process(self.production())
        self.NUM_PRODUCTS = 20
        self.next_time_stop = 0
        self.prod_and_requests = []
        self.reward = 0
        self.cumulative_reward = 0
        # Defining the observation and action spaces 
        # action space for choosing product 
        # self.action_space = spaces.Discrete(self.NUM_PRODUCTS)
        # action space for Yes/No action space 
        self.action_space = spaces.Discrete(2)
        self.observation_space = spaces.Box(0,1,shape = (self.NUM_PRODUCTS,),
                                            dtype = np.float32)
    
    def getObservation(self):
        # Calculate the states 
        states = []
        if self.machine.queue != None:
            for i in (self.machine.queue):
                states.append((self.relater(i)).number)
        #Checking the length of the states and filling the rest with zeros
        if len(states) < self.NUM_PRODUCTS:
            for i in range(self.NUM_PRODUCTS - len(states)):
                states.append(0)
        states = np.array(states).reshape(self.NUM_PRODUCTS,1)
        
        states = states.flatten()
        return states
    

# --------------------------------------------------------------------------------------------------------------------------------
# -----------------------OpenAI Gym functions--------------------------------------------------------------------
# --------------------------------------------------------------------------------------------------------------------------------
    
    def step(self, action):
        
        print("-------------------------------------------------------------------------------")
        print("Action chosen by the RL agent ", action)
        
        # Define params
        self.current_action = action
        self.action_taken = False 
        self.info = {}
        print("Current user of the machine ", envGym.machine.users)
        print(envGym.machine.queue)
        
        

        self.next_time_stop += self.time_step
        self.envSimpy.run(until = self.next_time_stop)
        # Get the observation states
        observation = self.getObservation()
        done = self.doneFn()
        info = self.info
        
        return observation, self.reward, done, info
    
    # ----------------------------------------------------------------
    def reset(self):
        self.envSimpy = simpy.Environment()
        self.machine = simpy.Resource(self.envSimpy,capacity = 1)
        self.time_start = self.envSimpy.now
        self.next_time_stop = self.time_start + 2
        self.time_step = 1 
        self.time_step_terminal = self.time_start + 100
        self.current_action = 0
        self.instances = []
        
        for i in range(self.NUM_PRODUCTS):
            self.instances.append(self.product(self,self.envSimpy,'Product_%d' % i,i/100, self.machine))
        
        # i is divided by hundred because the number has to obey the observation_space criteria which is 1 to 1. 
        self.observation = self.getObservation()
        
        return np.array(self.observation)  # reward, done, info can't be included

    
    def render(self, mode='human'):
        myFrame = ""
        #myFrame = "_:_:_:_:_:_:_:_:01:19:18:_:01:02:03::|02|"
        
        for item in enumerate(self.machine.queue):
            product = self.relater(item[1])
            myFrame = str(int((product.number)*100)) +':'+ myFrame
        for i in range(self.NUM_PRODUCTS-len(self.machine.queue)):
            myFrame =  'x' +':' + myFrame
        if self.relater(self.machine.users[0]) == None:
            prod_in_machine = 0
            machine_text = prod_in_machine 
        else:
            prod_in_machine = self.relater(self.machine.users[0])
            machine_text = int(prod_in_machine.number*100)
        myFrame = myFrame +  "  |" + str(machine_text) + "|"
        return myFrame

# --------------------------------------------------------------------------------------------------------------------------------
# -----------------------Miscellaneous functions--------------------------------------------------------------------
# --------------------------------------------------------------------------------------------------------------------------------
    def doneFn(self):
        # So the condition is, 
        #(no items in queue1 + queue2 + ...) AND 
        #(no machine is running)
        
        if self.machine.queue != None:
            lenQueue = len(self.machine.queue)
        else:
            lenQueue = 0 
        lenMachinesUsed = self.machine.count
        if lenQueue == 0 and lenMachinesUsed == 0:
            #print("length of queue ",lenQueue,"Machines used ", lenMachinesUsed)
            return True
        else:
            #print("length of queue ",lenQueue,"Machines used ", lenMachinesUsed)
            return False
        
    # A function to relate products and requests
    def relater(self,item):
        output_item = None
        # If the input is a request
        if type(item) == simpy.resources.resource.Request:
            for i, j in enumerate(self.prod_and_requests):
                if j[1] == item:
                    output_item = j[0]
                    return output_item
        else: #if the input is a product 
            for i, j in enumerate(self.prod_and_requests):
                if j[0] == item:
                    output_item = j[1]
                    return output_item    

# --------------------------------------------------------------------------------------------------------------------------------
# -----------------------Action related functions--------------------------------------------------------------------
# --------------------------------------------------------------------------------------------------------------------------------
    def choose_action(self):
        # sampling until we get a legal action
        self.action = envGym.action_space.sample()
        return self.action
    
    def take_action(self):
        # arrange the self.machine.queue based on the self.current_action
        self.action_taken = True 
        print("Taking the action....")
        print("Input machine queue ", self.machine.queue)
        if len(self.machine.queue) != 0:
            if self.current_action == 0: # if the answer is yes
                print("Action accepted")
                #print("The first item in the queue ", self.relater(self.machine.queue[0]).name, " is accepted ")
                print("Output machine queue ", self.machine.queue)
                return self.machine.queue # return the machine queue as is
            elif self.current_action == 1: # if the answer is no 
                # rearrange the machine queue 
                # Take the first element in the machine queue and put it in the last pos. 
                self.machine.queue.insert(len(self.machine.queue), self.machine.queue.pop(0))
                print("Action rejected")
                print("Output machine queue ", self.machine.queue)
                #print("The first item in the queue ", self.relater(self.machine.queue[0]).name, " is rejected ")
                return self.machine.queue
        else:
            return self.machine.queue

# --------------------------------------------------------------------------------------------------------------------------------
# -----------------------Product class definition--------------------------------------------------------------------
# --------------------------------------------------------------------------------------------------------------------------------

    class product(object):
        def __init__(self, envGym, envSimpy, name, number, machine):
            
            # Creating the required resources and environment
            self.envSimpy = envSimpy
            self.prod_type = random.randint(1,3) # the product type of the product.
            self.prod_state = 1 # the state of production. 1 implies raw material. 2 implies first operation done and so on. 
            self.production_time = random.randint(1,8)  
            self.name = name
            self.number = number
            self.machine = machine 
            self.production_end = random.randint(1,90)
            #self.action = self.envSimpy.process(self.production())
            #self.action_taken_event = envSimpy.event
            # Defining Events        
            #self.action_accepted_event = envSimpy.event()            
            # Defining processes
            #self.check_accepted_proc = envSimpy.process(self.check_accepted(envSimpy))


            
        def production(self):
            # the first step in production is requesting for a machine
            #print('entered production ' + self.name)
            with self.machine.request() as req:
                envGym.prod_and_requests.append([self,req])
                #print('waiting for the request to succeed ' + str(self.name))
                yield req
                print('Start production of ' + str(self.name) + ' at '+ str(self.envSimpy.now)  )
                print('Production time is ' + str(self.production_time))
                yield self.envSimpy.timeout(self.production_time)
                self.tardiness = self.production_end - self.envSimpy.now # +ve is good; -ve is bad 
                
                # End of production 
                print('End production of ' + str(self.name) + ' at ' + str(self.envSimpy.now))
                
                # Decide the reward 
                if self.tardiness > 0:
                    envGym.reward = 10 
                else: 
                    envGym.reward = 0
                    
                #yield self.action_accepted_event  # "passivate"
                
        
        def check_accepted(self, envSimpy): # sleep and production
            while True: # check in a continuous loop 
                if envGym.current_action == 0: # Is action accepted?
                    print("Action is accepted")
                    # Unsleeping the process 
                    self.action_accepted_event.succeed()
                    self.action_accepted_event = envSimpy.event()            
                else:
                    print("Action is rejected")
                    pass
        
        def passivate_production(self):
            while True:
                print("Passivating production at ", self.envSimpy.now)
                yield self.reactivate_production
                print("Production reactivate at ", self.envSimpy.now)
            #print('Remaining products to produce ')
            #print((self.machine.queue)) 